In [1]:
INTERIM_DATA_FOLDER = "../data/interim"
PROCESSED_DATA_FOLDER = "../data/processed"

In [2]:
import pandas as pd
import plotly.graph_objects as go

In [3]:
bmi_norm = pd.read_csv(f"{PROCESSED_DATA_FOLDER}/bmi_norm.csv")
ck_norm = pd.read_csv(f"{PROCESSED_DATA_FOLDER}/ck_norm.csv")
insuline_in_ck_patients = pd.read_csv(f"{INTERIM_DATA_FOLDER}/insulin_inputs_in_ck_pacients.csv")

In [4]:
bmi_norm["is_overweight"] = (bmi_norm["result_value"] >= 30).astype(int)
bmi_norm.groupby("is_overweight").count()

Unnamed: 0  subject_id  chartdate  seq_num  result_name  \
is_overweight                                                            
0                  108309      108309     108309   108309       108309   
1                   61576       61576      61576    61576        61576   

               result_value  
is_overweight                
0                    108309  
1                     61576

In [5]:
bmi_avg = bmi_norm.groupby(['subject_id'])['result_value'].mean().reset_index()

In [6]:
fig = go.Figure(data=[go.Histogram(x=bmi_avg["result_value"])])

fig.update_layout(
    title='Histogram of Result Values',
    xaxis_title='BMI',
    yaxis_title='Count'
)

fig.show()

In [7]:
ck_avg = ck_norm.groupby(['subject_id'])['valuenum'].mean().reset_index()
ck_bmi = ck_avg.merge(bmi_norm, on="subject_id", how="inner")[["valuenum", "result_value"]]


In [8]:
fig = go.Figure(data=[go.Histogram(x=ck_bmi["result_value"], y=ck_bmi["valuenum"])])

fig.update_layout(
    title='Histogram of Result Values',
    xaxis_title='BMI',
    yaxis_title='CK'
)

fig.show()

In [9]:
insuline_in_ck_patients.groupby("ordercategoryname")["ordercategoryname"].count()

ordercategoryname
01-Drips                    61893
05-Med Bolus                10710
06-Insulin (Non IV)        144211
12-Parenteral Nutrition      1461
Name: ordercategoryname, dtype: int64

In [10]:
def is_intravenous(row):
    if "Non IV" in row['ordercategoryname']:
        return 0
    return 1

insuline_in_ck_patients['is_intravenous'] = insuline_in_ck_patients.apply(is_intravenous, axis=1)
insuline_in_ck_patients

Unnamed: 0  subject_id   hadm_id   stay_id  caregiver_id  \
0              772    10002428  23473524  35479615         41151   
1              780    10002428  23473524  35479615         41151   
2              859    10002428  23473524  35479615         74793   
3              993    10002428  23473524  35479615         98628   
4             2842    10004235  24181354  34100191         24745   
...            ...         ...       ...       ...           ...   
218270     8978681    19999840  21033226  38978960         47270   
218271     8978718    19999840  21033226  38978960         47551   
218272     8978754    19999840  21033226  38978960         54462   
218273     8978775    19999840  21033226  38978960         54462   
218274     8978794    19999840  21033226  38978960         54462   

                  starttime              endtime            storetime  itemid  \
0       2156-05-19 22:41:00  2156-05-19 22:42:00  2156-05-19 22:42:00  223262   
1       2156-05-20 04:00:00  2156-05-20 04:01:00  2156-05-20 06:05:00  223262   
2       2156-05-13 09:43:00  2156-05-13 09:44:00  2156-05-13 09:43:00  223258   
3       2156-05-13 16:00:00  2156-05-13 16:01:00  2156-05-13 17:16:00  223258   
4       2196-02-25 00:54:00  2196-02-25 04:12:00  2196-02-25 00:54:00  223258   
...                     ...                  ...                  ...     ...   
218270  2164-09-15 22:12:00  2164-09-15 22:13:00  2164-09-15 22:12:00  223258   
218271  2164-09-15 11:00:00  2164-09-15 11:01:00  2164-09-15 11:11:00  223258   
218272  2164-09-16 10:11:00  2164-09-16 10:12:00  2164-09-16 10:11:00  223258   
218273  2164-09-16 16:53:00  2164-09-16 16:54:00  2164-09-16 16:53:00  223258   
218274  2164-09-17 09:30:00  2164-09-17 09:31:00  2164-09-17 09:30:00  223258   

           amount  ... ordercategorydescription  patientweight totalamount  \
0        0.000000  ...                Drug Push           48.4         NaN   
1        0.000000  ...                Drug Push           48.4         NaN   
2        2.000000  ...                Drug Push           48.4         NaN   
3        0.000000  ...                Drug Push           48.4         NaN   
4       13.197716  ...           Continuous Med          127.0       100.0   
...           ...  ...                      ...            ...         ...   
218270   4.000000  ...                Drug Push           77.5         NaN   
218271   2.000000  ...                Drug Push           77.5         NaN   
218272   2.000000  ...                Drug Push           77.5         NaN   
218273   4.000000  ...                Drug Push           77.5         NaN   
218274   4.000000  ...                Drug Push           77.5         NaN   

        totalamountuom  isopenbag continueinnextdept statusdescription  \
0                  NaN          0                  0   FinishedRunning   
1                  NaN          0                  0   FinishedRunning   
2                  NaN          0                  0   FinishedRunning   
3                  NaN          0                  0   FinishedRunning   
4                   ml          0                  0   ChangeDose/Rate   
...                ...        ...                ...               ...   
218270             NaN          0                  0   FinishedRunning   
218271             NaN          0                  0   FinishedRunning   
218272             NaN          0                  0   FinishedRunning   
218273             NaN          0                  0   FinishedRunning   
218274             NaN          0                  0   FinishedRunning   

       originalamount originalrate  is_intravenous  
0                0.00          0.0               0  
1                0.00          0.0               0  
2                2.00          2.0               0  
3                0.00          0.0               0  
4               96.25          4.0               1  
...               ...          ...             ...  
218270           4.00

In [11]:
x = ck_norm[["subject_id", "charttime", "valuenum", "valueuom"]].merge(
    insuline_in_ck_patients[["subject_id", "starttime", "endtime", "is_intravenous"]],
    on="subject_id",
    how="inner"
)

In [12]:
x[["valuenum", "is_intravenous"]]

valuenum  is_intravenous
0            29.0               0
1            29.0               0
2            29.0               0
3            29.0               0
4            31.0               0
...           ...             ...
1008265     147.0               0
1008266     147.0               0
1008267     147.0               0
1008268     147.0               0
1008269     147.0               0

[1008270 rows x 2 columns]

In [ ]:
import plotly.express as px

num_bins = 10
bin_edges = pd.qcut(x['valuenum'], num_bins, precision=1, duplicates='drop')

# Group by 'valuenum' and calculate the mean of 'is_intravenous'
grouped_df = x.groupby(bin_edges).mean()

# Convert the grouped data to a DataFrame
df_plot = pd.DataFrame({'valuenum': [interval.mid for interval in grouped_df.index], 'mean_is_intravenous': grouped_df['is_intravenous']})

# Create a scatter plot with lines connecting the dots
fig = px.line(df_plot, x='valuenum', y='mean_is_intravenous')

# Add labels and title
fig.update_layout(
    xaxis_title="valuenum",
    yaxis_title="Mean of is_intravenous",
    title="Mean of is_intravenous vs valuenum (Binned)"
)

# Display the plot
fig.show()

/tmp/ipykernel_229576/1452496564.py:7: FutureWarning:

The default value of numeric_only in DataFrameGroupBy.mean is deprecated. In a future version, numeric_only will default to False. Either specify numeric_only or select only columns which should be valid for the function.



In [ ]:
grouped_df = x.groupby(["valuenum"])["is_intravenous"].mean()

In [ ]:
fig = go.Figure(data=[go.Bar(x=grouped_df.index, y=grouped_df)])

# Add labels and title
fig.update_layout(
    xaxis_title="valuenum",
    yaxis_title="Mean of is_intravenous",
    title="Mean of is_intravenous vs valuenum"
)

# Display the plot
fig.show()

In [ ]:
x["is_intravenous"].isnull().sum()

16910

In [ ]:
x["valueuom"].isnull().sum()

666

In [ ]:
print(len(ck_norm))
print(len(insuline_in_ck_patients))

46536
218275
